In [2]:
# source: https://ourworldindata.org/co2-dataset-sources

In [3]:
import altair as alt
alt.data_transformers.disable_max_rows()
import pandas as pd
import geopandas as gpd
from vega_datasets import data

Load airports dataset

In [4]:
airport_url = 'airports.csv'
airports_df = pd.read_csv(airport_url, encoding='latin-1')
airports_df.head(5)

Airport ID                                         Name          City  \
0           1                               Goroka Airport        Goroka   
1           2                               Madang Airport        Madang   
2           3                 Mount Hagen Kagamuga Airport   Mount Hagen   
3           4                               Nadzab Airport        Nadzab   
4           5  Port Moresby Jacksons International Airport  Port Moresby   

            Country IATA  ICAO  Latitude   Longitude  Altitude TimeZone DST  \
0  Papua New Guinea  GKA  AYGA -6.081690  145.391998      5282       10   U   
1  Papua New Guinea  MAG  AYMD -5.207080  145.789002        20       10   U   
2  Papua New Guinea  HGU  AYMH -5.826790  144.296005      5388       10   U   
3  Papua New Guinea  LAE  AYNZ -6.569803  146.725977       239       10   U   
4  Papua New Guinea  POM  AYPY -9.443380  147.220001       146       10   U   

  Tz Database Time Zone     Type       Source  
0  Pacific/Port_Moresby  airport  OurAirports  
1  Pacific/Port_Moresby  airport  OurAirports  
2  Pacific/Port_Moresby  airport  OurAirports  
3  Pacific/Port_Moresby  airport  OurAirports  
4  Pacific/Port_Moresby  airport  OurAirports

Derive country continents from new dataset

In [5]:
continents = pd.read_csv('continents.csv')
continents

Entity      Code  Year Continent
0                 Abkhazia  OWID_ABK  2015      Asia
1              Afghanistan       AFG  2015      Asia
2    Akrotiri and Dhekelia  OWID_AKD  2015      Asia
3                  Albania       ALB  2015    Europe
4                  Algeria       DZA  2015    Africa
..                     ...       ...   ...       ...
280             Yugoslavia  OWID_YGS  2015    Europe
281                 Zambia       ZMB  2015    Africa
282               Zanzibar  OWID_ZAN  2015    Africa
283               Zimbabwe       ZWE  2015    Africa
284          Åland Islands       ALA  2015    Europe

[285 rows x 4 columns]

In [6]:
# drop code and year attributes
continents.drop(columns=['Code', 'Year'],inplace=True)
continents

Entity Continent
0                 Abkhazia      Asia
1              Afghanistan      Asia
2    Akrotiri and Dhekelia      Asia
3                  Albania    Europe
4                  Algeria    Africa
..                     ...       ...
280             Yugoslavia    Europe
281                 Zambia    Africa
282               Zanzibar    Africa
283               Zimbabwe    Africa
284          Åland Islands    Europe

[285 rows x 2 columns]

Certain country names do not match in the datasets so they must be normalized. To do this we must create a copy of the original dataframe and replace the unmatching countries with their continents. we end up with a mix of countries and continents in one column

In [7]:

# # for each row in airports, check if country is equal to entity (continents), append continent to it


temp_df = airports_df.copy()
for country in temp_df['Country'].to_list():
    for row in continents.values:
        if country.lower() in row[0].lower():
            temp_df['Country'] = temp_df['Country'].replace(
                country, row[1]) 
            break
mixed_continents_and_countries = temp_df['Country'].unique()
mixed_continents_and_countries

array(['Oceania', 'North America', 'Europe', 'Africa', 'South America',
       'Faroe Islands', 'Congo (Brazzaville)', 'Congo (Kinshasa)',
       'Swaziland', 'Asia', 'Czech Republic', 'Antarctica', 'West Bank',
       'Midway Islands', 'Macau', 'Burma', 'East Timor', 'Johnston Atoll',
       'Cocos (Keeling) Islands', 'Wake Island'], dtype=object)

Next we must extract these countries into their own list

In [8]:
unmatched_countries = []
for country in mixed_continents_and_countries:
    if country.lower() not in [x.lower() for x in continents['Continent'].to_list()]:
        unmatched_countries.append(country)
            
unmatched_countries

['Faroe Islands',
 'Congo (Brazzaville)',
 'Congo (Kinshasa)',
 'Swaziland',
 'Czech Republic',
 'West Bank',
 'Midway Islands',
 'Macau',
 'Burma',
 'East Timor',
 'Johnston Atoll',
 'Cocos (Keeling) Islands',
 'Wake Island']

Finally, we create a copy of the original dataframe and replace the unmatched country names

In [9]:
new_country_names = airports_df.copy()

for country in airports_df['Country'].to_list():
    for x in unmatched_countries:
        if x.lower() == country.lower():
            new_country_names['Country'] = new_country_names['Country'].replace(x)

Now we can finally add continent information to the dataset

In [10]:
continents_list = []
for country in new_country_names['Country'].to_list():
    for row in continents.values:
        if country.lower() in row[0].lower(): # 0 index for row is the country name
            continents_list.append(row[1]) # 1 index is continent
            break
new_country_names['Continent'] = continents_list
airports_df = new_country_names

# add number of airports per continent
airports_df["Airports per Continent"] = airports_df.groupby("Continent")["Continent"].transform("size")
airports_df["Airports per Country"] = airports_df.groupby("Country")["Country"].transform("size")
airports_df["Airports per City"] = airports_df.groupby("City")["City"].transform("size")
# export to new csv
airports_df.to_csv('airports_continents.csv',index=False)

 Load updated airports data
 

In [11]:
airports_url = 'airports_continents.csv'
airports_df = pd.read_csv(airports_url)
airports_df

Airport ID                                         Name          City  \
0              1                               Goroka Airport        Goroka   
1              2                               Madang Airport        Madang   
2              3                 Mount Hagen Kagamuga Airport   Mount Hagen   
3              4                               Nadzab Airport        Nadzab   
4              5  Port Moresby Jacksons International Airport  Port Moresby   
...          ...                                          ...           ...   
7693       14106                          Rogachyovo Air Base        Belaya   
7694       14107                        Ulan-Ude East Airport      Ulan Ude   
7695       14108                         Krechevitsy Air Base      Novgorod   
7696       14109                  Desierto de Atacama Airport       Copiapo   
7697       14110                           Melitopol Air Base     Melitopol   

               Country IATA  ICAO   Latitude   Longitude  Altitude TimeZone  \
0     Papua New Guinea  GKA  AYGA  -6.081690  145.391998      5282       10   
1     Papua New Guinea  MAG  AYMD  -5.207080  145.789002        20       10   
2     Papua New Guinea  HGU  AYMH  -5.826790  144.296005      5388       10   
3     Papua New Guinea  LAE  AYNZ  -6.569803  146.725977       239       10   
4     Papua New Guinea  POM  AYPY  -9.443380  147.220001       146       10   
...                ...  ...   ...        ...         ...       ...      ...   
7693            Russia   \N  ULDA  71.616699   52.478298       272       \N   
7694            Russia   \N  XIUW  51.849998  107.737999      1670       \N   
7695            Russia   \N  ULLK  58.625000   31.385000        85       \N   
7696             Chile  CPO  SCAT -27.261200  -70.779198       670       \N   
7697           Ukraine   \N  UKDM  46.880001   35.305000         0       \N   

     DST Tz Database Time Zone     Type       Source      Continent  \
0      U  Pacific/Port_Moresby  airport  OurAirports        Oceania   
1      U  Pacific/Port_Moresby  airport  OurAirports        Oceania   
2      U  Pacific/Port_Moresby  airport  OurAirports        Oceania   
3      U  Pacific/Port_Moresby  airport  OurAirports        Oceania   
4      U  Pacific/Port_Moresby  airport  OurAirports        Oceania   
...   ..                   ...      ...          ...            ...   
7693  \N                    \N  airport  OurAirports         Europe   
7694  \N                    \N  airport  OurAirports         Europe   
7695  \N                    \N  airport  OurAirports         Europe   
7696  \N                    \N  airport  OurAirports  South America   
7697  \N                    \N  airport  OurAirports         Europe   

      Airports per Continent  Airports per Country  Airports per City  
0                        621                    35                1.0  
1                        621                    35                1.0  
2                        621                    35                1.0  
3                        621                    35                1.0  
4                        621                    35                1.0  
...                      ...                   ...                ...  
7693                    1764                   265                1.0  
7694                    1764                   265                1.0  
7695                    1764                   265                1.0  
7696                     709                    46                2.0  
7697                    1764                    39                1.0  

[7698 rows x 18 columns]

In [12]:
emissions = pd.read_csv("annual-co2-emissions-per-country.csv")
emissions_2016 = emissions.where(emissions["Year"] == 2016)
emissions_2016 = emissions_2016.where(emissions_2016["Entity"] != "World")
emissions_2016.dropna(inplace=True)
emissions_2016

Entity Code    Year  Annual CO2 emissions
67           Afghanistan  AFG  2016.0             9067598.0
600              Albania  ALB  2016.0             4631977.0
706              Algeria  DZA  2016.0           158748370.0
978              Andorra  AND  2016.0              468992.0
1050              Angola  AGO  2016.0            27209698.0
...                  ...  ...     ...                   ...
30776            Vietnam  VNM  2016.0           226099800.0
30808  Wallis and Futuna  WLF  2016.0               25648.0
31152              Yemen  YEM  2016.0            10901535.0
31224             Zambia  ZMB  2016.0             5857442.0
31343           Zimbabwe  ZWE  2016.0            10533453.0

[219 rows x 4 columns]

Join emissions dataset with airports dataset

In [13]:
merged = pd.merge(airports_df,emissions_2016, how="inner", left_on="Country",right_on="Entity")
path ="aiports_emissions_merged.csv"
merged.to_csv(path)

In [14]:
world = alt.Chart(merged,width=150).mark_bar().encode(
    alt.Y('mean(Annual CO2 emissions):Q'),
    alt.X('Airports per Continent:Q',bin=True),
    alt.Color('mean(Annual CO2 emissions):Q',scale=alt.Scale(scheme="yelloworangered")),
   alt.Column('Continent:N'),
)
world

alt.Chart(...)